Poisson Equation
===

Import Netgen/NGSolve Python modules:

In [ ]:
from ngsolve import *
# from netgen.geom2d import unit_square
from netgen.occ import unit_square
from ngsolve.webgui import Draw

The unit_square is a predefined domain, use Netgen to generate a mesh:

In [ ]:
mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))
Draw (mesh);

Define a finite element space on that mesh. 

In [ ]:
fes = H1(mesh, order=3, dirichlet="left|right|bottom|top")
print ("ndof =", fes.ndof)

Define linear and bilinear-forms. 

$$
a(u,v) = \int \nabla u \nabla v
\qquad \text{and} \qquad
f(v) = \int f v
$$

Forms are expressed in terms of trial and test-functions:

In [ ]:
u = fes.TrialFunction()
v = fes.TestFunction()

f = LinearForm(fes)
f += 32*(y*(1-y)+x*(1-x))*v*dx

a = BilinearForm(fes)
a += grad(u)*grad(v)*dx

a.Assemble()
f.Assemble();

In [ ]:
print(f.vec)
print(a.mat)

Solve the problem:

In [ ]:
gfu = GridFunction(fes)
gfu.vec.data = a.mat.Inverse(fes.FreeDofs()) * f.vec

Plot the solution:

In [ ]:
Draw (gfu, mesh);

In [ ]:
Draw (-grad(gfu), mesh, "Flux", vectors= { "grid_size" : 40});

Calculate error:

In [ ]:
exact = 16*x*(1-x)*y*(1-y)
print ("L2-error:", sqrt(Integrate((gfu-exact)**2, mesh)))